# [Hodgkin-Huxley-Modell](https://de.wikipedia.org/wiki/Hodgkin-Huxley-Modell)

Es wird im folgenden zu erst ein kleines Stueck Nervenmembran betrachtet. 

Eine Membran besteht aus eine [Doppellipidschicht](https://de.wikipedia.org/wiki/Doppellipidschicht) und [Ionenkanäle](https://de.wikipedia.org/wiki/Ionenkanal). Beides bewirkt, dass ueber die Membran Stroeme fliessen.

Es gibt z.B.

- Na$^+$ Strom $I_{Na}$
- K$^+$ Strom $I_{K}$
- Leckstrom $I_L$
- Kapazitativen Strom $I_{cap}$
- Inizierter Strom durch eine Elektrode $I_{in}$

Es gilt auch an der Membran, dass elektrische Stroeme nicht verschwinden ([Kirschoffsche Knotenegel](https://de.wikipedia.org/wiki/Kirchhoffsche_Regeln)).

(1) $I_{Na} + I_K + I_L + I_{cap} = I_{in}$

_Wodurch sind diese Stroeme gegeben?_

## Kapazitative Stroeme

Fuer den [kapazitativen Strom](https://de.wikipedia.org/wiki/Elektrische_Kapazit%C3%A4t) gilt:

_Kapazitaet = Ladung / Spannung_ oder $C_m=Q / V$

Strom ist Ladung pro Zeit oder die Ableitung der Ladung nach der Zeit, $I=\frac{dQ}{dt}$. D.h. aus

$C_mV=Q$ 

wird durch Ableitung nach der Zeit auf beiden Seiten

$C_m\frac{dV}{dt} = I_{cap}$

Dies kann bereits in Gleichung (1) eingesetzt weden

## Ionenströme

Es gilt in erster Approximation das "URI"-Gesetz: _Membranspannung = Transmembranstrom * Membranwiederstand_.
Praktischerweise schreibt  man statt Wiederstand $R$, die Leitfaehigkeit $g=1/R$.

$I_K=g_K*(V-E_K)$  

$E_K$ ist das [Umkehrpotential](https://de.wikipedia.org/wiki/Membranpotential#Gleichgewichtspotential) fuer K$^+$

_Wie kommt man von URI auf dies?_

## Spannungsgesteurte Kannaele

Die Leitfaehigkeit eines [spannungsgesteuerten Ionenkanals](https://de.wikipedia.org/wiki/Spannungsgesteuerter_Ionenkanal) aendert sich mit der angelegten Membranspannung, $g_K(V)$. Es ist moeglich fuer verschiedene Kannaele eine __Aktivierungskurve__ zu messen. Diese sagt wieviel Prozent der Kannaele bei einer Spannung offen und geschlossen sind. Im folgenden sind einige definiert:

In [ ]:
from brian2 import *
import sympy
aktivierungskurven = {
    "h_inf" : "((0.07*exp(-(v/mV+58)/20))/(0.07*exp(-(v/mV+58)/20)+1/(1+exp(-0.1*(v/mV+28)))))",
    "h_tau" : "((1.*ms)/(0.07*exp(-(v/mV+58)/20)+1/(1+exp(-0.1*(v/mV+28)))))",
    "n_inf" : "(0.01*(v/mV+34)/(1-exp(-0.1*(v/mV+34))))/(0.01*(v/mV+34)/(1-exp(-0.1*(v/mV+34)))+0.125*exp(-(v/mV+44)/80))",
    "n_tau" : "((1.*ms)/(0.01*(v/mV+34)/(1-exp(-0.1*(v/mV+34)))+0.125*exp(-(v/mV+44)/80)))",
    "m_inf" : "((0.1*(v/mV+35))/(1-exp(-0.1*(v/mV+35)))/(0.1*(v/mV+35)/(1-exp(-0.1*(v/mV+35)))+4*exp(-(v/mV+60)/18)))"
}

Im flogenden sei die Aktivierungskurve des Na$^+$ Kannals aufgetragen.

In [ ]:
%matplotlib inline
from matplotlib import pyplot
import numpy
Na_akt = sympy.lambdify('v',aktivierungskurven['m_inf'],units)
V_list = numpy.linspace(-80,20,500) * mV
pyplot.plot(V_list/mV,[100*Na_akt(k) for k in V_list])
pyplot.xlabel('Membranpotential [mV]')
pyplot.ylabel('Prozent Kanal offen [%]')

Das Oeffnen und Schliessen der Kanaele fogt wieder differenzial Gleichungen erst Ordnung

$\frac{dm}{dt} = (m_{inf} - m)/\tau_m$

__Beachte:__ $m_{inf}(V)$ und $\tau_m(V)$ koennen bei jedem Membranpotential $V$ unterschiedlich sein.

### Weitere Parameter

Membrankapazitaet, Umkehrpotentiale und maximale Leitfaehigkeiten lassen sich experimentell bestimmen.

In [ ]:
parameter = {
    "C_m"  : "(1.0 * (ufarad/cm**2))",
    "E_K"  : "-90 * mV",
    "E_L"  : "-65 * mV",
    "E_Na" : "55 * mV",
    "g_K"  : "9 * (msiemens/cm**2)",
    "g_L"  : "0.1 * (msiemens/cm2)",
    "g_Na" : "35 * (msiemens/cm2)"
    }

### Stroeme und Gleichungen zusammensetzen

In [ ]:

membranstroeme = {
    "I_Na" : "g_Na*m_inf**3*h*(v-E_Na)",
    "I_K"  : "g_K*(n**4)*(v-E_K)",
    "I_L"  : "g_L*(v-E_L)"
  }  

differentialgleichungen = [
    "dh/dt = 5*(h_inf-h)/h_tau",
    "dn/dt = 5*(n_inf-n)/n_tau"
]

kirschoff = "C_m*dv/dt + I_Na + I_K + I_L - I_in"
differentialgleichungen += ["dv/dt = {}".format(sympy.solve(kirschoff,"dv/dt")[0])]
for k in differentialgleichungen:
    print(k)
    
from sympy import S
differentialgleichungen = [[S(j).subs(membranstroeme) for j in k.split("=")] for k in differentialgleichungen]
for k in differentialgleichungen:
    print(k)

differentialgleichungen = [[S(str(j)).subs(aktivierungskurven) for j in k] for k in differentialgleichungen]
differentialgleichungen = [[str(S(str(j)).subs(parameter)) for j in k] for k in differentialgleichungen]
differentialgleichungen = [[k[0],k[1]+":1"] if k[0]!="dv/dt" else [k[0],k[1]+":volt"] for k in differentialgleichungen]
differentialgleichungen = ["=".join([str(j) for j in k]) for k in differentialgleichungen]

Es wird [`brian2`](http://brian2.readthedocs.io/en/stable/) verwendet um die Gleichungen zu simmulieren.

In [ ]:
import brian2
brian2.defaultclock.dt=0.03*brian2.ms

I_list = ["0.13 * (uA/cm2)",
         "0.14 * (uA/cm2)",
         "0.15 * (uA/cm2)",
         "0.16 * (uA/cm2)",
         "0.17 * (uA/cm2)",
         "0.18 * (uA/cm2)",
         "0.19 * (uA/cm2)",
         "0.2 * (uA/cm2)",
          "0.21 * (uA/cm2)",
         "0.22 * (uA/cm2)"
         ]

eqs = Equations("""I_in : amp/meter**2""")
for k in differentialgleichungen:
    eqs += Equations(k)
neurongruppe = NeuronGroup(len(I_list), eqs,
                    threshold='v > -40*mV',
                    refractory='v > -40*mV',
                    method='rk4') # exponential_euler

neurongruppe.v = eval("-60 * mV", vars(units))
neurongruppe.I_in = [eval(k,vars(units)) for k in I_list]

monitor = StateMonitor(neurongruppe,variables=eqs.diff_eq_names,record=True)

net = Network(neurongruppe, monitor)
net.run(eval("100 * ms",vars(units)))

In [ ]:
%matplotlib inline
from matplotlib import pyplot

pyplot.plot(monitor.t/ms,monitor.v[0]/mV)
pyplot.xlabel("Zeit [ms]")
pyplot.ylabel("Membranpotential [mV]")

In [ ]:
%matplotlib inline
from matplotlib import pyplot

pyplot.plot(monitor.t/ms,monitor.n[0])
pyplot.xlabel("Zeit [ms]")
pyplot.ylabel("Membranpotential [mV]")

In [ ]:
%matplotlib inline
from matplotlib import pyplot

pyplot.plot(monitor.v[0]/mV,monitor.n[0]*100)
pyplot.ylabel("offene K$^+$ Kanal [%]")
pyplot.xlabel("Membranpotential [mV]")

In [ ]:
min_v = [min(k/mV) for k in monitor.v]
max_v = [max(k/mV) for k in monitor.v]
pyplot.plot([eval(k,vars(units)) for k in I_list],min_v,'.')
pyplot.plot([eval(k,vars(units)) for k in I_list],max_v,'.')
pyplot.xlabel('$I$ [$\mu$A/cm$^2$]')